# World Bank Data
![wb](https://www.un.org/sites/un2.un.org/files/field/image/world-bank-logo_0.jpg)

## download data using **wbgapi**


In [1]:
import wbgapi as wb
import pandas as pd
import time
import os
from datetime import datetime

import warnings
warnings.filterwarnings('ignore')

wb.source.info()


id    name                                                                  code      concepts  lastupdated
----  --------------------------------------------------------------------  ------  ----------  -------------
1     Doing Business                                                        DBS              3  2021-08-18
2     World Development Indicators                                          WDI              3  2025-07-01
3     Worldwide Governance Indicators                                       WGI              3  2024-11-05
5     Subnational Malnutrition Database                                     SNM              3  2016-03-21
6     International Debt Statistics                                         IDS              4  2025-02-26
11    Africa Development Indicators                                         ADI              3  2013-02-22
12    Education Statistics                                                  EDS              3  2024-06-25
13    Enterprise Surveys                                                    ESY              3  2022-03-25
14    Gender Statistics                                                     GDS              3  2025-07-31
15    Global Economic Monitor                                               GEM              3  2025-07-23
16    Health Nutrition and Population Statistics                            HNP              3  2025-07-02
18    IDA Results Measurement System                                        IDA              3  2021-07-23
19    Millennium Development Goals                                          MDG              3  2018-09-19
20    Quarterly Public Sector Debt                                          PSD              3  2025-07-30
22    Quarterly External Debt Statistics SDDS                               QDS              3  2025-08-14
23    Quarterly External Debt Statistics GDDS                               QDG              3  2025-07-31
25    Jobs                                                                  JOB              3  2025-07-01
27    Global Economic Prospects                                             GEP              3  2025-06-10
28    Global Findex database                                                FDX              3  2025-07-31
29    The Atlas of Social Protection: Indicators of Resilience and Equity   GSP              3  2025-08-25
30    Exporter Dynamics Database – Indicators at Country-Year Level         ED1              3  2016-03-31
31    Country Policy and Institutional Assessment                           CPI              3  2025-07-12
32    Global Financial Development                                          GFD              3  2022-09-23
33    G20 Financial Inclusion Indicators                                    G2F              3  2019-02-27
34    Global Partnership for Education                                      GPE              3  2013-04-12
35    Sustainable Energy for All                                            SE4              3  2018-06-30
37    LAC Equity Lab                                                        LEL              3  2016-04-06
38    Subnational Poverty                                                   SNP              3  2015-04-27
39    Health Nutrition and Population Statistics by Wealth Quintile         HNQ              3  2022-12-13
40    Population estimates and projections                                  HPP              3  2025-07-02
41    Country Partnership Strategy for India (FY2013 - 17)                  CPS              3  2015-05-22
43    Adjusted Net Savings                                                  WAT              3  2023-06-08
45    Indonesia Database for Policy and Economic Research                   IDD              3  2022-08-11
46    Sustainable Development Goals                                         SDG              3  2022-07-22
50    Subnational Population                                                SNT              3  2017-09-21
54    Joint External Debt Hub        

In [5]:
# Define indicators
indicators = {
    'SP.DYN.LE00.IN': 'Life expectancy at birth, total (years)',
    'NY.GDP.PCAP.CD': 'GDP per capita (current US$)',
    'SP.POP.TOTL': 'Population, total',
    'NY.GDP.MKTP.CD': 'GDP (current US$)',
    'SP.DYN.TFRT.IN': 'Fertility rate, total (births per woman)',
    'SP.DYN.IMRT.IN': 'Mortality rate, infant (per 1,000 live births)',
    'SE.ADT.LITR.ZS': 'Literacy rate, adult total (% of people ages 15 and above)',
    'SH.XPD.CHEX.PC.CD': 'Current health expenditure per capita (current US$)'
}

def safe_wb_fetch(indicator, years=range(1960, 2024), max_retries=3):
    """Safely fetch World Bank data with error handling and retries"""
    for attempt in range(max_retries):
        try:
            print(f"  Fetching {indicator} (attempt {attempt + 1})...")
            data = wb.data.DataFrame(
                indicator, 
                time=years,
                skipAggs=True,  # Skip aggregate regions
                skipBlanks=True  # Skip missing values
            )
            print(f"  ✓ Successfully fetched {indicator}")
            print(f"  ✓ Data shape: {data.shape}")
            print(f"  ✓ Sample columns: {list(data.columns)[:5]}")
            return data
        except Exception as e:
            print(f"  ✗ Error fetching {indicator} (attempt {attempt + 1}): {e}")
            if attempt < max_retries - 1:
                time.sleep(2)  # Wait before retry
            else:
                print(f"  ✗ Failed to fetch {indicator} after {max_retries} attempts")
                return None

def process_indicator_data(data, indicator_code, indicator_name):
    """Process raw World Bank data into clean format"""
    if data is None:
        return None
    
    # Reset index and reshape from wide to long format
    data_clean = data.reset_index()
    data_clean = data_clean.melt(
        id_vars=['economy'], 
        var_name='year', 
        value_name='value'
    )
    
    # Clean up year column - handle 'YR' prefix if present
    data_clean['year'] = data_clean['year'].astype(str)
    data_clean['year'] = data_clean['year'].str.replace('YR', '', regex=False)
    
    # Convert to int, handling any remaining issues
    try:
        data_clean['year'] = pd.to_numeric(data_clean['year'], errors='coerce')
        data_clean = data_clean.dropna(subset=['year'])
        data_clean['year'] = data_clean['year'].astype(int)
    except Exception as e:
        print(f"  Warning: Year conversion issue: {e}")
        return None
    
    data_clean['indicator_code'] = indicator_code
    data_clean['indicator_name'] = indicator_name
    data_clean = data_clean.dropna(subset=['value'])
    
    return data_clean

def get_country_metadata():
    """Get country metadata including names, regions, and income levels"""
    try:
        print("Fetching country metadata...")
        countries = wb.economy.DataFrame()
        
        # Check the actual columns available
        print(f"  Available columns: {list(countries.columns)}")
        
        # Create continent mapping
        continent_mapping = {
            'EAS': 'Asia',
            'ECS': 'Europe', 
            'LCN': 'Americas',
            'MEA': 'Middle East & Africa',
            'NAC': 'North America',
            'SAS': 'South Asia',
            'SSF': 'Sub-Saharan Africa'
        }
        
        # Handle different possible column names
        if 'region' in countries.columns:
            countries['continent'] = countries['region'].map(continent_mapping)
        else:
            countries['continent'] = 'Unknown'
        
        # Create standardized column names based on what's available
        country_columns = {}
        
        # Map common column variations
        for col in countries.columns:
            col_lower = col.lower()
            if col_lower in ['id', 'code', 'economy']:
                country_columns['country_code'] = col
            elif col_lower in ['name', 'economy_name']:
                country_columns['country_name'] = col
            elif col_lower in ['region']:
                country_columns['region'] = col
            elif col_lower in ['incomelevel', 'income_level', 'income']:
                country_columns['income_level'] = col
            elif col_lower in ['capitalcity', 'capital_city', 'capital']:
                country_columns['capital_city'] = col
        
        # Select available columns
        available_columns = []
        column_mapping = {}
        
        if 'country_code' in country_columns:
            available_columns.append(country_columns['country_code'])
            column_mapping[country_columns['country_code']] = 'country_code'
        if 'country_name' in country_columns:
            available_columns.append(country_columns['country_name'])
            column_mapping[country_columns['country_name']] = 'country_name'
        if 'region' in country_columns:
            available_columns.append(country_columns['region'])
            column_mapping[country_columns['region']] = 'region'
        if 'income_level' in country_columns:
            available_columns.append(country_columns['income_level'])
            column_mapping[country_columns['income_level']] = 'income_level'
        if 'capital_city' in country_columns:
            available_columns.append(country_columns['capital_city'])
            column_mapping[country_columns['capital_city']] = 'capital_city'
        
        # Add continent column
        available_columns.append('continent')
        
        # Select and rename columns
        countries_clean = countries[available_columns].copy()
        countries_clean = countries_clean.rename(columns=column_mapping)
        
        print(f"✓ Fetched metadata for {len(countries_clean)} countries")
        print(f"  Final columns: {list(countries_clean.columns)}")
        return countries_clean
        
    except Exception as e:
        print(f"✗ Error fetching country metadata: {e}")
        print("  Continuing without country metadata...")
        return None

def create_wide_format_dataframe(all_data, country_metadata):
    """Create a single wide-format dataframe with all indicators as columns"""
    
    # Combine all data
    long_data = pd.concat(all_data, ignore_index=True)
    
    # Create a mapping for cleaner column names
    column_mapping = {
        'SP.DYN.LE00.IN': 'lifeExp',
        'NY.GDP.PCAP.CD': 'gdpPercap', 
        'SP.POP.TOTL': 'pop',
        'NY.GDP.MKTP.CD': 'gdp',
        'SP.DYN.TFRT.IN': 'fertility',
        'SP.DYN.IMRT.IN': 'infantMortality',
        'SE.ADT.LITR.ZS': 'literacy',
        'SH.XPD.CHEX.PC.CD': 'healthExpend'
    }
    
    # Map indicator codes to cleaner names
    long_data['indicator_clean'] = long_data['indicator_code'].map(column_mapping)
    
    # Pivot to wide format: each indicator becomes a column
    wide_data = long_data.pivot_table(
        index=['economy', 'year'], 
        columns='indicator_clean', 
        values='value', 
        aggfunc='first'
    ).reset_index()
    
    # Flatten column names
    wide_data.columns.name = None
    
    # Add country metadata if available
    if country_metadata is not None and not country_metadata.empty:
        print(f"  Merging with country metadata...")
        print(f"  Country metadata columns: {list(country_metadata.columns)}")
        
        # Find the right column for merging
        merge_column = None
        if 'country_code' in country_metadata.columns:
            merge_column = 'country_code'
        elif len(country_metadata.columns) > 0:
            # Use the first column as country code
            merge_column = country_metadata.columns[0]
            country_metadata = country_metadata.rename(columns={merge_column: 'country_code'})
            merge_column = 'country_code'
        
        if merge_column:
            wide_data = wide_data.merge(
                country_metadata, 
                left_on='economy', 
                right_on=merge_column, 
                how='left'
            )
            
            # Set country name
            if 'country_name' in country_metadata.columns:
                wide_data['country'] = wide_data['country_name'].fillna(wide_data['economy'])
            else:
                wide_data['country'] = wide_data['economy']
                
            # Set continent with fallback
            if 'continent' in country_metadata.columns:
                wide_data['continent'] = wide_data['continent'].fillna('Unknown')
            else:
                wide_data['continent'] = 'Unknown'
        else:
            print("  No suitable merge column found, using economy codes as country names")
            wide_data['country'] = wide_data['economy']
            wide_data['continent'] = 'Unknown'
    else:
        print("  No country metadata available, using economy codes as country names")
        wide_data['country'] = wide_data['economy']
        wide_data['continent'] = 'Unknown'
    
    # Add iso_alpha column for plotly compatibility
    wide_data['iso_alpha'] = wide_data['economy']
    
    # Reorder columns in a logical way
    base_columns = ['country', 'economy', 'iso_alpha', 'year']
    if 'continent' in wide_data.columns:
        base_columns.insert(1, 'continent')
    
    # Add indicator columns
    indicator_columns = [col for col in wide_data.columns if col in column_mapping.values()]
    
    # Add any remaining columns
    other_columns = [col for col in wide_data.columns 
                    if col not in base_columns and col not in indicator_columns]
    
    final_columns = base_columns + indicator_columns + other_columns
    
    # Keep only columns that exist
    final_columns = [col for col in final_columns if col in wide_data.columns]
    wide_data = wide_data[final_columns]
    
    return wide_data

def main():
    """Main function to download all World Bank data and create single dataframe"""
    
    print("=" * 60)
    print("WORLD BANK DATA DOWNLOADER")
    print("Creating Single Wide-Format Dataframe")
    print("=" * 60)
    print(f"Starting download at: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}")
    print(f"Total indicators to download: {len(indicators)}")
    
    # Create data directory
    if not os.path.exists('world_bank_data'):
        os.makedirs('world_bank_data')
    
    # Get country metadata
    country_metadata = get_country_metadata()
    
    # Download each indicator
    all_data = []
    successful_downloads = 0
    
    for i, (code, name) in enumerate(indicators.items(), 1):
        print(f"\n[{i}/{len(indicators)}] Processing: {name}")
        print("-" * 50)
        
        # Fetch data
        raw_data = safe_wb_fetch(code)
        
        if raw_data is not None:
            # Process data
            processed_data = process_indicator_data(raw_data, code, name)
            
            if processed_data is not None:
                all_data.append(processed_data)
                successful_downloads += 1
                print(f"  ✓ Successfully processed {len(processed_data)} data points")
        
        # Be respectful to the API
        time.sleep(1)
    
    print("\n" + "=" * 60)
    print("CREATING SINGLE WIDE-FORMAT DATAFRAME")
    print("=" * 60)
    
    if all_data:
        # Create the single wide-format dataframe
        final_dataframe = create_wide_format_dataframe(all_data, country_metadata)
        
        print(f"✓ Final dataframe shape: {final_dataframe.shape}")
        print(f"✓ Years covered: {final_dataframe['year'].min()} - {final_dataframe['year'].max()}")
        print(f"✓ Countries: {final_dataframe['country'].nunique()}")
        print(f"✓ Columns: {list(final_dataframe.columns)}")
        
        # Save the single dataframe
        timestamp = datetime.now().strftime('%Y%m%d_%H%M%S')
        
        # CSV format
        csv_filename = f"world_bank_data/world_bank_single_dataframe_{timestamp}.csv"
        final_dataframe.to_csv(csv_filename, index=False)
        print(f"✓ Saved single dataframe as CSV: {csv_filename}")
        
        # Excel format
        excel_filename = f"world_bank_data/world_bank_single_dataframe_{timestamp}.xlsx"
        final_dataframe.to_excel(excel_filename, index=False, sheet_name='WorldBankData')
        print(f"✓ Saved single dataframe as Excel: {excel_filename}")
        
        # Display sample of the data
        print(f"\n✓ Sample of the final dataframe:")
        print(final_dataframe.head(10).to_string())
        
        # Display data availability summary
        print(f"\n✓ Data availability by indicator:")
        for col in ['lifeExp', 'gdpPercap', 'pop', 'gdp', 'fertility', 'infantMortality', 'literacy', 'healthExpend']:
            if col in final_dataframe.columns:
                count = final_dataframe[col].notna().sum()
                print(f"  {col}: {count:,} non-null values")
        
        print(f"\n✓ SINGLE DATAFRAME READY FOR USE!")
        print(f"✓ Variable name: final_dataframe")
        print(f"✓ Shape: {final_dataframe.shape}")
        
        return final_dataframe
        
    else:
        print("✗ No data was successfully downloaded!")
        return None
    
    print("\n" + "=" * 60)
    print("DOWNLOAD SUMMARY")
    print("=" * 60)
    print(f"Total indicators requested: {len(indicators)}")
    print(f"Successfully downloaded: {successful_downloads}")
    print(f"Failed downloads: {len(indicators) - successful_downloads}")
    print(f"Completion time: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}")
    print("\n" + "=" * 60)

if __name__ == "__main__":
    # Check if wbgapi is installed
    try:
        import wbgapi as wb
        wb_dataframe = main()
        
        if wb_dataframe is not None:
            print(f"\n🎉 SUCCESS! Your World Bank dataframe is ready!")
            print(f"📊 Access it using the variable: wb_dataframe")
            print(f"📏 Shape: {wb_dataframe.shape}")
            print(f"📋 Columns: {list(wb_dataframe.columns)}")
            
            # Quick usage example
            print(f"\n💡 Quick usage examples:")
            print(f"   wb_dataframe.head()  # View first 5 rows")
            print(f"   wb_dataframe.info()  # Data types and info")
            print(f"   wb_dataframe['country'].unique()  # All countries")
            print(f"   wb_dataframe[wb_dataframe['year'] == 2020]  # Data for 2020")
            
    except ImportError:
        print("Error: wbgapi is not installed.")
        print("Please install it using: pip install wbgapi")
    except Exception as e:
        print(f"An error occurred: {e}")
        print("Please check your internet connection and try again.")

WORLD BANK DATA DOWNLOADER
Creating Single Wide-Format Dataframe
Starting download at: 2025-09-02 05:13:34
Total indicators to download: 8
Fetching country metadata...
  Available columns: ['name', 'aggregate', 'longitude', 'latitude', 'region', 'adminregion', 'lendingType', 'incomeLevel', 'capitalCity']
✓ Fetched metadata for 266 countries
  Final columns: ['country_name', 'region', 'income_level', 'capital_city', 'continent']

[1/8] Processing: Life expectancy at birth, total (years)
--------------------------------------------------
  Fetching SP.DYN.LE00.IN (attempt 1)...
  ✓ Successfully fetched SP.DYN.LE00.IN
  ✓ Data shape: (217, 64)
  ✓ Sample columns: ['YR1960', 'YR1961', 'YR1962', 'YR1963', 'YR1964']
  ✓ Successfully processed 13854 data points

[2/8] Processing: GDP per capita (current US$)
--------------------------------------------------
  Fetching NY.GDP.PCAP.CD (attempt 1)...
  ✓ Successfully fetched NY.GDP.PCAP.CD
  ✓ Data shape: (214, 64)
  ✓ Sample columns: ['YR1960'

# Chloropleth maps

In [3]:
data = pd.read_csv('world_bank_data/world_bank_single_dataframe_20250818_035723.csv')
print(data)#.describe(include='all'))


      country continent economy iso_alpha  year  fertility           gdp  \
0         ABW   Unknown     ABW       ABW  1960      4.567           NaN   
1         ABW   Unknown     ABW       ABW  1961      4.422           NaN   
2         ABW   Unknown     ABW       ABW  1962      4.262           NaN   
3         ABW   Unknown     ABW       ABW  1963      4.107           NaN   
4         ABW   Unknown     ABW       ABW  1964      3.940           NaN   
...       ...       ...     ...       ...   ...        ...           ...   
13868     ZWE   Unknown     ZWE       ZWE  2019      3.748  2.571566e+10   
13869     ZWE   Unknown     ZWE       ZWE  2020      3.754  2.686856e+10   
13870     ZWE   Unknown     ZWE       ZWE  2021      3.765  2.724051e+10   
13871     ZWE   Unknown     ZWE       ZWE  2022      3.767  3.278966e+10   
13872     ZWE   Unknown     ZWE       ZWE  2023      3.724  3.523137e+10   

         gdpPercap  healthExpend  infantMortality  lifeExp   literacy  \
0             

In [4]:
import plotly.express as px

indicators = {
    'lifeExp': 'Life expectancy at birth, total',
    'gdpPercap': 'GDP per capita',
    'pop': 'Population, total',
    'gdp': 'GDP  (Gross Domestic Product)',
    'fertility': 'Fertility rate, total (births per woman)',
    'infantMortality': 'Mortality rate, infant',
    'literacy': 'Literacy rate, adult total (% of people ages 15 and above)',
    'healthExpend': 'Current health expenditure per capita'
}

# randomly choose a colormap from the list
import random
#random.seed(4)
my_list = ['aggrnyl', 'agsunset', 'algae', 'amp', 'armyrose', 'balance',
             'blackbody', 'bluered', 'blues', 'blugrn', 'bluyl', 'brbg',
             'brwnyl', 'bugn', 'bupu', 'burg', 'burgyl', 'cividis', 'curl',
             'darkmint', 'deep', 'delta', 'dense', 'earth', 'edge', 'electric',
             'emrld', 'fall', 'geyser', 'gnbu', 'gray', 'greens', 'greys',
             'haline', 'hot', 'hsv', 'ice', 'icefire', 'inferno', 'jet',
             'magenta', 'magma', 'matter', 'mint', 'mrybm', 'mygbm', 'oranges',
             'orrd', 'oryel', 'oxy', 'peach', 'phase', 'picnic', 'pinkyl',
             'piyg', 'plasma', 'plotly3', 'portland', 'prgn', 'pubu', 'pubugn',
             'puor', 'purd', 'purp', 'purples', 'purpor', 'rainbow', 'rdbu',
             'rdgy', 'rdpu', 'rdylbu', 'rdylgn', 'redor', 'reds', 'solar',
             'spectral', 'speed', 'sunset', 'sunsetdark', 'teal', 'tealgrn',
             'tealrose', 'tempo', 'temps', 'thermal', 'tropic', 'turbid',
             'turbo', 'twilight', 'viridis', 'ylgn', 'ylgnbu', 'ylorbr',
             'ylorrd'] 

# Define appropriate ranges for each indicator
color_ranges = {
    'lifeExp': [40, 85],
    'gdpPercap': [0, 50000],
    'pop': [100000, 1400000000],  # 100K to 1.4B
    'gdp': [1e9, 25e12],  # 1 billion to 25 trillion
    'fertility': [1, 7],
    'infantMortality': [0, 100],
    'literacy': [20, 100],
    'healthExpend': [0, 8000]
}

# Custom colorbar configurations
colorbar_configs = {
    'lifeExp': {
        'title': 'Life Expectancy (years)',
        'tickmode': 'array',
        'tickvals': [40, 50, 60, 70, 80],
        'ticktext': ['40', '50', '60', '70', '80+']
    },
    'gdpPercap': {
        'title': 'GDP per Capita (USD)',
        'tickmode': 'array',
        'tickvals': [0, 10000, 25000, 50000],
        'ticktext': ['$0', '$10K', '$25K', '$50K+']
    },
    'pop': {
        'title': 'Population',
        'tickmode': 'array',
        'tickvals': [1e6, 10e6, 100e6, 1e9],
        'ticktext': ['1M', '10M', '100M', '1B+']
    },
    'gdp': {
        'title': 'Total GDP (USD)',
        'tickmode': 'array',
        'tickvals': [1e9, 100e9, 1e12, 10e12],
        'ticktext': ['$1B', '$100B', '$1T', '$10T+']
    },
    'fertility': {
        'title': 'Fertility Rate',
        'tickmode': 'array',
        'tickvals': [1, 2, 3, 5, 7],
        'ticktext': ['1', '2', '3', '5', '7+']
    },
    'infantMortality': {
        'title': 'Infant Mortality (per 1,000)',
        'tickmode': 'array',
        'tickvals': [0, 10, 25, 50, 100],
        'ticktext': ['0', '10', '25', '50', '100+']
    },
    'literacy': {
        'title': 'Literacy Rate (%)',
        'tickmode': 'array',
        'tickvals': [20, 40, 60, 80, 100],
        'ticktext': ['20%', '40%', '60%', '80%', '100%']
    },
    'healthExpend': {
        'title': 'Health Expenditure per Capita (USD)',
        'tickmode': 'array',
        'tickvals': [0, 1000, 3000, 6000, 8000],
        'ticktext': ['$0', '$1K', '$3K', '$6K', '$8K+']
    }
}

for var, titre in indicators.items():
    # Create a choropleth map with fixed color range
    fig = px.choropleth(
        data,
        locations="iso_alpha",
        color=var,
        hover_name="country",
        animation_frame="year",
        projection="natural earth",
        title=titre,
        range_color=color_ranges[var],  # Fixed range for each indicator
        color_continuous_scale=random.choice(my_list)  # Consistent random color scale
    )
    
    # Update the colorbar with custom configuration
    fig.update_layout(coloraxis_colorbar=colorbar_configs[var])
    
    # Save as HTML file
    fig.write_html(f"world_bank_data/world_bank_{var}.html")
    
    # Show the map
    fig.show()



import geopandas as gpd
import matplotlib.pyplot as plt
import geodatasets
import requests
import zipfile
import os
import io

# Load the world map from the local shapefile
print(f"Loading world map from {shp_file}...")
world = gpd.read_file(shp_file)

if not world.empty:
    print("World map loaded successfully.")
else:
    # URL for the GeoJSON file
    url = "https://naciscdn.org/naturalearth/10m/cultural/ne_10m_admin_0_countries.zip"
    local_zip_path = "ne_10m_admin_0_countries.zip"
    extracted_dir = "ne_10m_countries"
    
    # 1. Download the file and save it locally
    print(f"Downloading world map data from {url}...")
    try:
        response = requests.get(url)
        response.raise_for_status()  # Raise an exception for bad status codes
        with open(local_zip_path, 'wb') as f:
            f.write(response.content)
        print("Download complete.")
    except requests.exceptions.RequestException as e:
        print(f"Error downloading the file: {e}")
        exit()
    
    # 2. Unzip the file
    print(f"Extracting {local_zip_path}...")
    try:
        with zipfile.ZipFile(local_zip_path, 'r') as zip_ref:
            zip_ref.extractall(extracted_dir)
        print("Extraction complete.")
    except zipfile.BadZipFile:
        print("Error: The downloaded file is not a valid zip archive.")
        exit()
    except Exception as e:
        print(f"Error during file extraction: {e}")
        exit()
    
    # Find the shapefile (.shp) in the extracted directory
    shp_file = None
    for root, dirs, files in os.walk(extracted_dir):
        for file in files:
            if file.endswith('.shp'):
                shp_file = os.path.join(root, file)
                break
        if shp_file:
            break
    
    if shp_file is None:
        print("Error: Could not find a shapefile (.shp) in the extracted directory.")
        exit()

    # Load the world map from the local shapefile
    print(f"Loading world map from {shp_file}...")
    world = gpd.read_file(shp_file)

# Load the built-in world map using the new geodatasets package
#url = "https://naciscdn.org/naturalearth/10m/cultural/ne_10m_admin_0_countries.zip"
#world = gpd.read_file(url)
#print(world)

# colormap list
colors = ['Accent', 'Accent_r', 'Blues', 'Blues_r', 'BrBG', 'BrBG_r', 'BuGn', 'BuGn_r', 
          'BuPu', 'BuPu_r', 'CMRmap', 'CMRmap_r', 'Dark2', 'Dark2_r', 'GnBu', 'GnBu_r', 
          'Grays', 'Grays_r', 'Greens', 'Greens_r', 'Greys', 'Greys_r', 'OrRd', 'OrRd_r', 
          'Oranges', 'Oranges_r', 'PRGn', 'PRGn_r', 'Paired', 'Paired_r', 'Pastel1', 
          'Pastel1_r', 'Pastel2', 'Pastel2_r', 'PiYG', 'PiYG_r', 'PuBu', 'PuBuGn', 'PuBuGn_r', 
          'PuBu_r', 'PuOr', 'PuOr_r', 'PuRd', 'PuRd_r', 'Purples', 'Purples_r', 'RdBu', 
          'RdBu_r', 'RdGy', 'RdGy_r', 'RdPu', 'RdPu_r', 'RdYlBu', 'RdYlBu_r', 'RdYlGn', 
          'RdYlGn_r', 'Reds', 'Reds_r', 'Set1', 'Set1_r', 'Set2', 'Set2_r', 'Set3', 'Set3_r',
          'Spectral', 'Spectral_r', 'Wistia', 'Wistia_r', 'YlGn', 'YlGnBu', 'YlGnBu_r', 'YlGn_r',
          'YlOrBr', 'YlOrBr_r', 'YlOrRd', 'YlOrRd_r', 'afmhot', 'afmhot_r', 'autumn', 'autumn_r',
          'berlin', 'berlin_r', 'binary', 'binary_r', 'bone', 'bone_r', 'brg', 'brg_r', 'bwr',
          'bwr_r', 'cividis', 'cividis_r', 'cool', 'cool_r', 'coolwarm', 'coolwarm_r', 'copper',
          'copper_r', 'cubehelix', 'cubehelix_r', 'flag', 'flag_r', 'gist_earth', 'gist_earth_r',
          'gist_gray', 'gist_gray_r', 'gist_grey', 'gist_grey_r', 'gist_heat', 'gist_heat_r',
          'gist_ncar', 'gist_ncar_r', 'gist_rainbow', 'gist_rainbow_r', 'gist_stern', 'gist_stern_r',
          'gist_yarg', 'gist_yarg_r', 'gist_yerg', 'gist_yerg_r', 'gnuplot', 'gnuplot2', 
          'gnuplot2_r', 'gnuplot_r', 'gray', 'gray_r', 'grey', 'grey_r', 'hot', 'hot_r', 'hsv',
          'hsv_r', 'inferno', 'inferno_r', 'jet', 'jet_r', 'magma', 'magma_r', 'managua', 'managua_r',
          'nipy_spectral', 'nipy_spectral_r', 'ocean', 'ocean_r', 'pink', 'pink_r', 'plasma',
          'plasma_r', 'prism', 'prism_r', 'rainbow', 'rainbow_r', 'seismic', 'seismic_r', 'spring', 
          'spring_r', 'summer', 'summer_r', 'tab10', 'tab10_r', 'tab20', 'tab20_r', 'tab20b', 
          'tab20b_r', 'tab20c', 'tab20c_r', 'terrain', 'terrain_r', 'turbo', 'turbo_r', 'twilight',
          'twilight_r', 'twilight_shifted', 'twilight_shifted_r', 'vanimo', 'vanimo_r', 'viridis',
          'viridis_r', 'winter', 'winter_r']

# Perform the merge using the country codes
# We use an inner join to only keep countries that exist in both datasets
merged_data = world.merge(data, left_on='SOV_A3', right_on='iso_alpha', how='inner')
#print(merged_data.head())

for var, titre in indicators.items():
    # Create the plot
    fig, ax = plt.subplots(1, 1, figsize=(15, 10))
    
    # Plot the 'fertility' data from the merged GeoDataFrame
    merged_data.plot(column=var, 
                     ax=ax, 
                     legend=True,
                     legend_kwds={'label': var,
                                  'orientation': "vertical"},
                     cmap=random.choice(colors))  # You can choose a different colormap
    
    # Add a title
    ax.set_title(titre)
    
    # Remove the axis frame for a cleaner, map-like look
    ax.set_axis_off()
    
    # Display the plot
    plt.show()